In [1]:
from lie_algebra_multiplicity import *
def WeightsWithMultiplicity1InG2(l):
    tot = 3 * l - 1
    if tot < 0:
        return []
    else:
        m1 = 0
        m2 = 0
        solns = []
        if tot % 3 == 0:
            m2 = tot / 3
        elif tot % 3 == 1:
            m1 = 2
            m2 = (tot - 4) / 3
        elif tot % 3 == 2:
            m1 = 1
            m2 = (tot - 2) / 3
        
        while m1 >= 0 and m2 >= 0:
            solns.append([m1,m2])
            m1 += 3
            m2 -= 2
            
        return solns
    
def getAltSetsG(l):
    weights = WeightsWithMultiplicity1InG2(l)
    altsets = [findAltSet("G2", lamb = [0, l], mu = weight, simple = False) for weight in weights]
    return altsets

def multCheckG(l):
    weights = WeightsWithMultiplicity1InG2(l)
    mults = [calculateMultiplicity("G2", lamb = [0,l], mu = weight, q_analog = True, simple=False) for weight in weights]
    return mults
    
    
test = 1
print WeightsWithMultiplicity1InG2(test)
print getAltSetsG(test)
print multCheckG(test)

[[1, 0]]


[[1, s1]]
[q^2]


In [4]:
from lie_algebra_multiplicity import *
def noElementsGreaterThan(arr, maxVal):
    for i in arr:
        if i > maxVal:
            return False
        
    return True

def countIndices(partition, r):
    ret = [0 for i in range(0,r)]
    for i in partition:
        ret[i-1] += 1
        
    return ret

def WeightsWithMultiplicity1InA(r, l):
    mod = r+1
    multiple = l / mod
    distance = l % mod
    all_weights = []
    
    while multiple >= 0:
        partitions = Partitions(distance,max_part=r).list()
        weights = [countIndices(partition, r) for partition in partitions]
        all_weights  = all_weights + weights
        multiple -= 1
        distance += mod
        
    return all_weights

def getAltSetsA(r, l):
    weights = WeightsWithMultiplicity1InA(r, l)
    altsets = [findAltSet("A" + str(r), lamb = [l], mu = weight, simple = False) for weight in weights]
    return altsets

def multCheckA(r, l):
    weights = WeightsWithMultiplicity1InA(r, l)
    mults = [calculateMultiplicity("A" + str(r), lamb = [l], mu = weight, q_analog = True, simple=False) for weight in weights]
    return mults
        
test_l =5
test_r = 7
print WeightsWithMultiplicity1InA(test_r, test_l)
#print multCheckA(test_r, test_l)
#print getAltSetsA(test_r, test_l)

print [len(alt) for alt in getAltSetsA(test_r, test_l)]

[[0, 0, 0, 0, 1, 0, 0], [1, 0, 0, 1, 0, 0, 0], [0, 1, 1, 0, 0, 0, 0], [2, 0, 1, 0, 0, 0, 0], [1, 2, 0, 0, 0, 0, 0], [3, 1, 0, 0, 0, 0, 0], [5, 0, 0, 0, 0, 0, 0]]


[10, 4, 2, 2, 1, 1, 1]


In [0]:
def allEvenElements(arr):
    for i in arr:
        if i % 2 == 1:
            return False
        
    return True

def WeightsWithMultiplicity1InB(r, l):
    if r < 2:
        return []
    tot = l - 1
    m_r = int((tot * 2) / r)
    m_r = m_r if m_r % 2 == 0 else m_r - 1
    all_weights = []
    
    while m_r >= 0:
        sub_tot = int(tot - ((r * m_r)/2)) # this is always an integer, but sage automatically casts some things and causes issues with partitioning
        partitions = Partitions(sub_tot,max_part=r-1).list()
        weights = [countIndices(partition, r-1) for partition in partitions]
        for weight in weights:
            if allEvenElements(weight):
                weight.append(m_r)
                all_weights.append(weight)
        m_r -= 2
        
    return all_weights

def getAltSetsB(r, l):
    weights = WeightsWithMultiplicity1InB(r, l)
    altsets = [findAltSet("B" + str(r), lamb = [l], mu = weight, simple = False) for weight in weights]
    return altsets

def multCheckB(r, l):
    weights = WeightsWithMultiplicity1InB(r, l)
    mults = [calculateMultiplicity("B" + str(r), lamb = [l], mu = weight, q_analog = False, simple=False) for weight in weights]
    return mults

test_r = 7
test_l = 7
print WeightsWithMultiplicity1InB(test_r, test_l)
#print multCheckB(test_r, test_l)
print getAltSetsB(test_r, test_l)

In [0]:
def generateTables():
    types = [("A", WeightsWithMultiplicity1InA,1,lambda r,l: [l if i == 0 else 0 for i in range(0,r)]),("B",WeightsWithMultiplicity1InB,2, lambda r,l: [l if i == 0 else 0 for i in range(0,r)])]
    data = {"A":{}, "B":{}}
    for (T,muFunc,start,lambFunc) in types:
        for r in range(start,6):
            data[T][r] = []
            for l in range(1,11):
                lamb = lambFunc(r, l)
                mus = muFunc(r, l)
                mults = []
                alts = []
                for mu in mus:
                    mults.append(calculateMultiplicity(T + str(r), lamb = lamb, mu = mu, q_analog = True, simple=False))
                    alts.append(findAltSet(T + str(r), lamb=lamb, mu=mu, simple=False))
                data[T][r].append((l, lamb, mus,mults, alts))
    return data

x = generateTables()

tex = open("tables.tex", "w+")
for T in x:
    for r in x[T]:
        tex.write("\\begin{table}[h!]\n\\centering\\begin{tabular}{|c|c|c|}\n")
        tex.write("\\hline\n")
        tex.write("\\multicolumn{3}{|c|}{$r=" + str(r) + "$}\\\\\n")
        tex.write("\\hline\n")
        tex.write("$\\lambda = \\ell\\omega_1$ & $\\mu\\in M_\\ell$ & $m_q(\\lambda,\\mu)$ \\\\\n")
        tex.write("\\hline\n")
        for (l, lamb, mus, mults, alts) in x[T][r]:
            if len(mus) == 0:
                continue
            multrow = len(mus)
            tex.write("\\multirow{" + str(multrow) + "}{*}{$\\ell=" + str(l) + "$}")
            for i in range(0, len(mus)):
                mu = ""
                for j in range(0,len(mus[i])):
                    if mus[i][j] != 0:
                        coeff = mus[i][j]
                        mu += (str(coeff) if coeff != 1 else "") + "\\omega_" + str(j + 1) + "+"
                mu = "0" if mu == "" else mu[:-1]
                alt = str(alts[i]).replace("*","").replace("[","").replace("]","").replace("s","s_")
                mult_temp = str(mults[i]).replace("-", "+-").split("+")
                mult = ""
                for term in mult_temp:
                    temp = term.split("^")
                    if len(temp) >= 2:
                        mult += temp[0] + "^{" + temp[1] + "}+"
                    else:
                        mult += temp[0] + "+"
                mult = mult.replace("+-", "-")[:-1]
                if i == len(mus) - 1:
                    tex.write("& $" + mu + "$ & $" + mult + "$ \\\\\n")
                else:
                    tex.write("& $" + mu + "$ & $" + mult + "$ \\cline{2-3}\\\\\n")
            tex.write("\\hline\n")
        tex.write("\\end{tabular}\n\\caption{Weights of multiplicity 1 in type " + T + str(r) + "}\n\\end{table}\n\n")
        
tex.close()

In [0]:
x = "1214"
print x[:-1]

In [1]:
from lie_algebra_multiplicity import *
x = changeFundToSimple("B7", [7,0,0,0,0,0,0]).list()
name = "A10"
lamb = [2,0,0,0,0,0,0,0,0,0]
mu = [0,1,0,0,0,0,0,0,0,0]
alt = findAltSet(name, lamb, mu, simple=False)
print alt
rho = RootSystem(name).ambient_space().rho()

l_w = convertWeightParameters(name, lamb, False)
m_w = convertWeightParameters(name, mu, False)

basis_change = getStandardToSimple(name)

print "lambda: ", basis_change * vector(list(Eval(l_w)))
print "mu: ", basis_change * vector(list(Eval(m_w)))

for elm in alt:
    print elm
    print elm.action(l_w+rho)
    print (m_w + rho)
    init = elm.action(l_w+rho) - (m_w + rho)
    print init
    init = basis_change * vector(list(Eval(init)))
    init = roundIfAppropriate(init)
    print init
    print (-1)**elm.length() * calculatePartition(name, list(init), q_analog = True)

print calculateMultiplicity(name, lamb, mu, q_analog=True, simple=False)

[1]
lambda:  (1.8181818181818181, 1.6363636363636362, 1.4545454545454544, 1.2727272727272725, 1.0909090909090908, 0.909090909090909, 0.7272727272727271, 0.5454545454545452, 0.36363636363636337, 0.18181818181818155, -2.220446049250313e-16)
mu:  (0.8181818181818182, 1.6363636363636365, 1.4545454545454546, 1.272727272727273, 1.090909090909091, 0.9090909090909093, 0.7272727272727275, 0.5454545454545456, 0.3636363636363638, 0.181818181818182, 2.220446049250313e-16)
1
(130/11, 97/11, 86/11, 75/11, 64/11, 53/11, 42/11, 31/11, 20/11, 9/11, -2/11)
(119/11, 108/11, 86/11, 75/11, 64/11, 53/11, 42/11, 31/11, 20/11, 9/11, -2/11)
(1, -1, 0, 0, 0, 0, 0, 0, 0, 0, 0)
(1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
q
q
